# Análisis Dataset de "Inside Airbnb" : ESTAMBUL


<center><img src="https://www.miladoviajero.com/wp-content/uploads/Estambul-mapa.jpg"></center>

---> Aqui se puede ver todo el trabajo en streamlit : ('https://proyectoairbnb-ukj20covyxr.streamlit.app/')

# 1. Introducción

"Inside Airbnb" es un sitio web que proporciona información sobre los alojamientos disponibles para alquilar en la plataforma de Airbnb. El objetivo de este sitio web es mostrar el impacto que tiene esta plataforma en el mercado de la vivienda en cada ciudad. 
Para este análisis, hemos seleccionado la ciudad de Estambul, conocida por su rica historia, cultura y su gastronomía. A menudo se le llama la "Ciudad de las Mil Mezquitas".

¿Sabías que es la única ciudad del mundo que se encuentra entre dos continentes, Asia y Europa? 


**Objetivo de análisis**:

El objetivo de este análisis es explorar la oferta de alojamientos en Estambul. Examinaremos varios aspectos, como la distribución de los alojamientos, las tendencias de precios, los tipos de alojamientos disponibles y las características de los anfitriones.
Las preguntas clave que buscamos responder son:
* ¿Cómo se distribuyen los alojamientos en Estambul en general?
* ¿Cómo varían los precios en diferentes tipos de alojamientos?
* ¿Cuáles son los tipos de alojamientos más comunes en Estambul?
* ¿Qué podemos aprender sobre los anfitriones de estos alojamientos?

Al abordar estas preguntas, buscamos obtener información sobre la dinámica del mercado de Airbnb en Estambul y comprender mejor las características del panorama de alojamientos en la ciudad



# 2. Librerías

In [1]:
import numpy as np
import pandas as pd


#to make graphs
import matplotlib.pyplot as plt
import seaborn as sns

#to make the plotly graphs
import plotly.graph_objs as go
import plotly.express as px

#to make maps
import geopandas as gpd

# warnings
import warnings
warnings.filterwarnings("ignore", category=FutureWarning)
warnings.filterwarnings("ignore", category=RuntimeWarning)

# 3. Lectura de Datasets

### Lectura de los datasets

In [2]:
listings = pd.read_csv("data/listings.csv", index_col= "id")
listings_details = pd.read_csv("data/listings_details.csv", index_col= "id", low_memory=False)

calendar = pd.read_csv('data/calendar.csv', parse_dates=['date'], index_col=['listing_id']).reset_index()
reviews_details = pd.read_csv("data/reviews_details.csv", parse_dates=['date']).reset_index()
neighbourhoods = pd.read_csv("data/neighbourhoods.csv").reset_index()

# 4. Limpieza de Datos

Fuente: http://insideairbnb.com/get-the-data.html 

En la web podemos encontrarnos con 7 documentos:

* listings.cvs 
* listings_details.cvs
* calendar.csv
* reviews.csv
* reviews_details.csv
* neighbourhoods.csv
* neighbourhoods.geojson

Se utilizaron los datasets: listings.cvs y listings_details.cvs para realizar los análisis y el modelo predictivo. Y el documento neighbourhoods.geojson para realizar los mapas.


### Funciones de análisis

Definimos estas funciones para poder usarla en los 6 datasets y analizar su contenido

In [3]:
def reporte (df):   
    """ Esta función recibe un df y nos imprime un reporte inicial del df"""
    
    print('El df esta formado por: ', df.shape[0], 'filas y', df.shape[1], 'columnas')
    print('Cantidad de valores duplicados: ',df.duplicated().sum())
    print('Cantidad de valores nulos: ', df.isnull().sum().sum())
    # print('Primeras filas del df:')
    # return df.head(3) # Imprimimos las primeras filas para ver las columnas y asi tener una primera vista de lo que hay en el df

In [4]:
def percentage_null (df):
    missing_data = pd.isnull(df).sum()
    missing_data_percentage = missing_data/len(df)*100 #Calculamos el % del los datos faltantes en cada columna
    nulos_totales= missing_data_percentage.sort_values(ascending = False) #Ordenamos de mayor a menor
    nulos_totales = pd.DataFrame(nulos_totales,columns=["% nulos"])
    return nulos_totales.round(2)

## 4.1 Dataset: listings

#### Contenido de las columnas

* ***id***: Airbnb's unique identifier for the listing
* ***name***: Name of the listing
* ***host_id***: Airbnb's unique identifier for the host/user
* ***host_name***: Name of the host. Usually just the first name(s).
* ***neighbourhood_group***: The neighbourhood group as geocoded using the latitude and longitude against neighborhoods as defined by open or public digital shapefiles.
* ***neighbourhood***: The neighbourhood as geocoded using the latitude and longitude against neighborhoods as defined by open or public digital shapefiles.
* ***latitude***: Uses the World Geodetic System (WGS84) projection for latitude and longitude.
* ***longitude***: Uses the World Geodetic System (WGS84) projection for latitude and longitude.
* ***room_type***: All homes are grouped into the following three room types: 1. Entire home/apt 2. Private room 3. Shared room|Hotel]
* ***price***: daily price in local currency. Note, $ sign may be used despite locale
* ***minimum_nights***: minimum number of night stay for the listing (calendar rules may be different)
* ***number_of_reviews***: The number of reviews the listing has
* ***last_review***: The date of the last/newest review
* ***calculated_host_listings_count***: The number of listings the host has in the current scrape, in the city/region geography.
* ***availability_365***: avaliability_x. The availability of the listing x days in the future as determined by the calendar. Note a listing may be available because it has * been booked by a guest or blocked by the host.
* ***number_of_reviews_ltm***: The number of reviews the listing has (in the last 12 months)
* ***license***: The licence/permit/registration number


### Informe inicial

In [5]:
# Usamos esta función para tener en un solo informe que es lo que tenemos en nuestro df
reporte(listings)

El df esta formado por:  41501 filas y 17 columnas
Cantidad de valores duplicados:  8
Cantidad de valores nulos:  118101


## 4.2 Dataset: listings_details

### Informe inicial

In [6]:
reporte(listings_details)

El df esta formado por:  41501 filas y 74 columnas
Cantidad de valores duplicados:  0
Cantidad de valores nulos:  503873


Dado que el este data frame tiene 74 columnas seleccionamos las columnas que necesitamos para nuestro analisis.
Cremaos la variable columnas con un total de 19 variables que hemos seleccionado para nuestro análisis.


In [7]:
columns = ["property_type", "accommodates", "first_review", "review_scores_value", "review_scores_cleanliness", "review_scores_location", "review_scores_accuracy", "review_scores_communication", "review_scores_checkin", "review_scores_rating", "maximum_nights", "listing_url", "host_is_superhost", "host_about", "host_response_time", "host_response_rate", "host_listings_count","number_of_reviews_ltm","reviews_per_month"]

## 4.3 Merge : listings & listings_details

In [8]:
df = pd.merge(listings, listings_details[columns], on='id', how='left')

In [9]:
# Dataset para poner en app antes de limpieza.
#guardamos nuestro df 
df.to_csv('df.csv', header=True, index=False)

In [10]:
reporte(df)

El df esta formado por:  41501 filas y 36 columnas
Cantidad de valores duplicados:  0
Cantidad de valores nulos:  321467


### Eliminación de columnas con valores nulos

In [11]:
# Vemos el % de columnas con valores nulos
percentage_null(df).T

license  neighbourhood_group  host_about  review_scores_checkin  \
% nulos    100.0                100.0       59.65                  42.55   

         review_scores_location  review_scores_value  \
% nulos                   42.55                42.55   

         review_scores_communication  review_scores_accuracy  \
% nulos                        42.55                   42.55   

         review_scores_cleanliness  reviews_per_month_y  ...  longitude  \
% nulos                      42.55                42.26  ...        0.0   

         host_id  room_type  price  minimum_nights  number_of_reviews  \
% nulos      0.0        0.0    0.0             0.0                0.0   

         calculated_host_listings_count  availability_365  \
% nulos                             0.0               0.0   

         number_of_reviews_ltm_x  accommodates  
% nulos                      0.0           0.0  

[1 rows x 36 columns]

Las columnas license y neighbourhood_group presentan un 100% de porcentaje nulos se procede a eliminarlas.


In [12]:
# Como las columnas license y neighbourhood_group presentan un 100% de porcentaje nulos se procede a eliminarlas
df = df.drop(columns=['neighbourhood_group','license'])

In [13]:
# La columna host_about es la descripción que hace el host para presentarse, como es una variable que no vamos a utilizar
# procedemos a quiratla de nuestro df.
df = df.drop(columns=['host_about'])

In [14]:
# En la columna name vamos a reemplazar los nulos por la palabra "no_name"
df['name'] = df['name'].fillna("no_name")

Con respecto a resto de las columnas que contienen null y corresponden a reviews no las vamos a reemplazar ya que es mejor trabajar con la información real.

In [15]:
percentage_null(df).T

review_scores_value  review_scores_location  review_scores_checkin  \
% nulos                42.55                   42.55                  42.55   

         review_scores_cleanliness  review_scores_accuracy  \
% nulos                      42.55                   42.55   

         review_scores_communication  reviews_per_month_y  \
% nulos                        42.55                42.26   

         reviews_per_month_x  last_review  review_scores_rating  ...  \
% nulos                42.26        42.26                 42.26  ...   

         calculated_host_listings_count  number_of_reviews  minimum_nights  \
% nulos                             0.0                0.0             0.0   

         price  room_type  longitude  latitude  neighbourhood  host_name  \
% nulos    0.0        0.0        0.0       0.0            0.0        0.0   

         accommodates  
% nulos           0.0  

[1 rows x 33 columns]

### Tranformación de columnas

In [16]:
pd.set_option('display.max_columns', None)

In [17]:
# Usamos el método info para ver como estan compuestas nuestras columnas
print(df.info())

<class 'pandas.core.frame.DataFrame'>
Index: 41501 entries, 25436 to 857756437907689464
Data columns (total 33 columns):
 #   Column                          Non-Null Count  Dtype  
---  ------                          --------------  -----  
 0   name                            41501 non-null  object 
 1   host_id                         41501 non-null  int64  
 2   host_name                       41501 non-null  object 
 3   neighbourhood                   41501 non-null  object 
 4   latitude                        41501 non-null  float64
 5   longitude                       41501 non-null  float64
 6   room_type                       41501 non-null  object 
 7   price                           41501 non-null  int64  
 8   minimum_nights                  41501 non-null  int64  
 9   number_of_reviews               41501 non-null  int64  
 10  last_review                     23964 non-null  object 
 11  reviews_per_month_x             23964 non-null  float64
 12  calculated_host_list

In [18]:
# Podemos ver que el dtype de las columnas estan correctos por lo que no procedemos a realizar ningun cambio
df['host_response_rate'] = pd.to_numeric(df['host_response_rate'].str.strip('%'))

In [19]:
# Cambiamos el contenido de la columna host_is_superhost a través de un diccionario:
# df['host_is_superhost'] = df['host_is_superhost'].replace({'f': False, 't': True})

Se crea una nueva variable (price_euro) con la columna price convertida a euro ya que esta columna viene en moneda local (Lira turca) y así poder tener una mejor comprensión y percepción. 

El tipo de cambio utilizado es de la web de la unión europea:
https://commission.europa.eu/funding-tenders/procedures-guidelines-tenders/information-contractors-and-beneficiaries/exchange-rate-inforeuro_es
El tipo de cambio a la fecha fecha: 26/06/2023 es 1 TRY = 0.04564 EUR


In [20]:
df['price_euro'] = df['price']*0.04564 
df['price_euro'] = df['price_euro'].round(2).astype('int64')

In [21]:
# Ahora si imprimimos el head del df con el que vamos a continuar:
df.head()

name  host_id  host_name  \
id                                                                            
25436   In the forest Sea view Two minutes to the city.   105823      Yesim   
27271              Lovely apartment in perfect location   117026      Mutlu   
304011            Beyoglu / Central with Beautiful View  1564870     Living   
304029               Zero km to City Center -- Friendly  1564916       Esen   
28277                  Duplex Apartment 11 with Terrace   121607  Alen Ziya   

       neighbourhood  latitude  longitude        room_type  price  \
id                                                                  
25436       Besiktas  41.07883   29.03863  Entire home/apt   2085   
27271        Beyoglu  41.03254   28.98153  Entire home/apt   1044   
304011       Beyoglu  41.03537   28.97316  Entire home/apt   1118   
304029         Sisli  41.05156   28.99052     Private room    384   
28277          Sisli  41.04672   28.98402  Entire home/apt   1857   

        minimum_nights  number_of_reviews last_review  reviews_per_month_x  \
id                                                                           
25436               25                  0         NaN                  NaN   
27271               10                  4  2022-11-01                 0.04   
304011              28                 28  2023-03-18                 0.26   
304029               2                 36  2023-01-05                 0.27   
28277               10                  8  2022-11-26                 0.35   

        calculated_host_listings_count  availability_365  \
id                                                         
25436                                1               348   
27271                                1               266   
304011                               2               240   
304029                               1                94   
28277                               20               361   

        number_of_reviews_ltm_x              property_type  accommodates  \
id                                                                         
25436                         0         Entire rental unit             3   
27271                         1         Entire rental unit             2   
304011                        7         Entire rental unit             4   
304029                        1       Private room in loft             2   
28277                         6  Entire serviced apartment             5   

       first_review  review_scores_value  review_scores_cleanliness  \
id                                                                    
25436           NaN                  NaN                        NaN   
27271    2014-10-20                 5.00                       4.75   
304011   2014-05-12                 4.63                       4.93   
304029   2012-05-07                 4.91                       4.94   
28277    2021-05-15                 4.75                       4.75   

        review_scores_location  review_scores_accuracy  \
id                                                       
25436                      NaN                     NaN   
27271                     5.00                    5.00   
304011                    4.59                    4.85   
304029                    4.79                    4.88   
28277                     5.00                    5.00   

        review_scores_communication  review_scores_checkin  \
id                                                           
25436                           NaN                    NaN   
27271                          5.00                   5.00   
304011                         4.93                   4.96   
304029                         5.00                   5.00   
28277                          5.00                   4.88   

        review_scores_rating  maximum_nights  \
id                                             
25436                    NaN            1125   
27271                   5.00

## 4.4 Dataset: calendar

Este Dataframe muestra la disponibiiad que tiene el alojamiento desde el 2023-03-31  al  2024-04-02.
No lo vamos a ultilizar para nuestro análisis por lo cual no vamos a avanzar con su análisis

### Informe inicial

In [22]:
reporte(calendar)

El df esta formado por:  15146021 filas y 7 columnas


Cantidad de valores duplicados:  0
Cantidad de valores nulos:  68


In [23]:
calendar.head(3)

listing_id       date available      price adjusted_price  minimum_nights  \
0       25436 2023-03-31         f  $2,085.00      $2,085.00            25.0   
1       25436 2023-04-01         f  $2,085.00      $2,085.00            25.0   
2       25436 2023-04-02         f  $2,085.00      $2,085.00            25.0   

   maximum_nights  
0          1125.0  
1          1125.0  
2          1125.0

In [24]:
print('Período de fechas de análisis', calendar['date'].min(), ' - ', calendar['date'].max())

Período de fechas de análisis 2023-03-31 00:00:00  -  2024-04-02 00:00:00


## 4.4 Dataset: reviews_details

Este dataset contiene las reviwes de que han tenido los alojamientos, como esta información la podemos obtener en los datasets de listings en esta oportunidad no se usarán para el análisis.

Período de análisis 2010-06-14 - 2023-04-01

### Informe inicial

In [25]:
reporte(reviews_details)

El df esta formado por:  416940 filas y 7 columnas


Cantidad de valores duplicados:  0
Cantidad de valores nulos:  21


In [26]:
reviews_details.head()

index  listing_id                  id       date  reviewer_id  \
0      0       27271            21619434 2014-10-20     17033378   
1      1      304029             1242627 2012-05-07      2224284   
2      2       27271           260206599 2018-05-04     34086382   
3      3       27271  535927099037466665 2022-01-09    419733560   
4      4       27271  750456812858706901 2022-11-01    132525657   

     reviewer_name                                           comments  
0         Hortense  En l'absence de Mutlu, sa voisine adorable nou...  
1  Tim And Nandini  Stayed with my girlfriend at Esen's apartment....  
2            Marie  Appartement très agréable, bien situé.<br/>Mut...  
3           Daniel                                                5/5  
4             Paul  The apartment certainly looks better than in p...

In [27]:
print('Período de análisis', reviews_details['date'].min(), ' - ', reviews_details['date'].max())

Período de análisis 2010-06-14 00:00:00  -  2023-04-01 00:00:00


## 4.5 Dataset: neighbourhoods

Este dataframe contiene una lista de todos los vecindarios que presenta nuetro df.

Como esta información también la podemos obtener en los datasets de listings en esta oportunidad no se usarán para el análisis.


### Informe inicial

In [28]:
reporte(neighbourhoods)

El df esta formado por:  39 filas y 3 columnas
Cantidad de valores duplicados:  0
Cantidad de valores nulos:  39


In [29]:
# Cantidad de vecindarios:
neighbourhoods['neighbourhood'].sort_values().count()

39

In [30]:
neighbourhoods.head()

index  neighbourhood_group neighbourhood
0      0                  NaN        Adalar
1      1                  NaN    Arnavutkoy
2      2                  NaN      Atasehir
3      3                  NaN       Avcilar
4      4                  NaN      Bagcilar

# 5. Análisis Exporatorio de Datos

Ahora tenemos un df listo para realizar el análisis exploratorio. TEniedo en cuenta que los nulos corresponden a las columnas de reviews.


In [31]:
reporte(df)

El df esta formado por:  41501 filas y 34 columnas
Cantidad de valores duplicados:  0
Cantidad de valores nulos:  213686


Para responder a las preguntas planteadas al inicio, se dividió el análisis en cuatro secciones principales.

### ¿Cómo se distribuyen los alojamientos en Estambul en general?

Estambul está dividida por 39 distritos en los cuales podemos ver, según la gráfica y en el mapa, que la mayoría de los hospedajes se encuentran en los distritos de: Beyoglu, Sisli, Kadikoy y Fatih. Estos distritos tienen características únicas que los hacen atractivos para los visitantes y locales.

* Beyoglu: es reconocido por ser el lugar donde las comunidades extranjeras establecieron embajadas e iglesias en el pasado. En el siglo XX, este distrito fue testigo de la construcción de grandes hoteles y tiendas de lujo, lo que lo convierte en un centro de elegancia y sofisticación.
* Sisli: se destaca como el distrito de cines y lugares de ocio. Aquí se encuentran diversas salas de conciertos, teatros y otros espacios de entretenimiento. Es un lugar animado y vibrante que ofrece una amplia gama de actividades culturales para disfrutar.
* Kadikoy: por otro lado, es un distrito residencial conocido mercado de pescado y productos agrícolas. Tanto los turistas como los locales aprovechan la oportunidad de explorar este mercado y adquirir especias, tés y frutos secos frescos. Además, Kadikoy cuenta con una gran cantidad de restaurantes, cafeterías y tiendas que reflejan la vida cotidiana de la ciudad.
* Fatih: este distrito alberga el barrio histórico de Estambul. Aquí se encuentra la gran Mezquita de Fatih, una de las más grandes de la ciudad, así como el antiguo acueducto romano y otros impresionantes edificios y monumentos históricos. Fatih es un lugar de gran importancia cultural y atrae a los amantes de la historia y la arquitectura.


In [32]:
colors = ['#AF1D56', '#FFDE59', '#CB6CE6', '#FF914D']

In [35]:
# Cantidad de Barios

neighbourhood_count=df['neighbourhood'].value_counts().sort_values(ascending=True)
fig1 = px.bar(neighbourhood_count, orientation='h', 
       template= "plotly_dark",
       color_discrete_sequence = [colors[3]],
       height=800    
       )
fig1.update_layout(
       title='Distribución de distritos',
       xaxis=dict(title='cantidades'),
       yaxis=dict(title=''),
       showlegend=False
    )


In [36]:
dfneighbourhood = pd.DataFrame(neighbourhood_count)
dfneighbourhood

count
neighbourhood       
Sultanbeyli       36
Catalca           45
Sultangazi        48
Bayrampasa        72
Esenler           74
Sancaktepe        81
Gungoren          97
Silivri           99
Cekmekoy         126
Gaziosmanpasa    140
Tuzla            183
Beykoz           221
Arnavutkoy       224
Buyukcekmece     266
Zeytinburnu      278
Beylikduzu       356
Adalar           375
Pendik           437
Eyup             441
Kartal           444
Sile             471
Kucukcekmece     483
Avcilar          489
Basaksehir       497
Sariyer          501
Umraniye         535
Bakirkoy         536
Bahcelievler     596
Bagcilar         781
Maltepe          797
Atasehir         884
Kagithane       1304
Uskudar         1352
Esenyurt        1622
Besiktas        2649
Fatih           4036
Kadikoy         4442
Sisli           6254
Beyoglu         9229

In [38]:
# Cantidad de Alojamientos por Distritos

df_neighbourhood = pd.DataFrame(neighbourhood_count)
df_neighbourhood = df_neighbourhood.reset_index()
adam = gpd.read_file("data/neighbourhoods.geojson")
fig3 = px.choropleth_mapbox(df_neighbourhood, geojson=adam, featureidkey='properties.neighbourhood',locations ="neighbourhood",color ='count', 
                            color_continuous_scale='magma', title="Distritos de Estambul",zoom=10, hover_data = ['neighbourhood','count'],
                            mapbox_style="carto-positron",width=1000, height=750,center = {"lat": 41.0037, "lon": 28.9737})
fig3.update(layout_coloraxis_showscale=True)
fig3.update_layout( paper_bgcolor="#fff",font_color="#AF1D56",title_font_size=40, title_x = 0.5)
fig3.update_layout(legend=dict(title=""))
fig3.show()

### ¿Cómo varía el precio de los alojamientos?

En el análisis de precios de los alojamientos en Estambul, se observa que el precio medio es de TRY 2.007,34 (liras turcas), lo que equivale a aproximadamente EUR 91,12 al tipo de cambio del 26/06/23. Para tener una mejor comprensión y comparación, los valores se muestran en euros.
El distrito de Beylikduzu se destaca como el distrito con el mayor valor medio de alojamientos, alcanzando los EUR 344,29. Esto contrasta con los distritos que presentan una mayor cantidad de hospedajes ofrecidos, donde los precios son más moderados:

* Beyoglu: EUR 88,11
* Sisli: EUR 82,55
* Kadikoy: EUR 108,3
* Fatih: EUR 91,03

Esto puede deberse a que el distrito de Beylikduzu ha experimentado un rápido desarrollo en los últimos años, presenta un gran desarrollo urbano, comodidades y una gran demanda de viviendas de alta calidad


In [49]:
price_mean = df.groupby('neighbourhood')['price_euro'].mean().round(2).sort_values(ascending=True)
dfprecio = pd.DataFrame(price_mean)
dfprecio = dfprecio.reset_index()
#ahora graficamos con plotly
fig3 = px.area(dfprecio, x="neighbourhood", y="price_euro",
        template= "plotly_dark", 
        title = "Average daily price based on location in Amsterdam",
        color_discrete_sequence = [colors[2]] 
        )

fig3.update_layout(
       title='Precio promedio de alojamientos por distrito',
       xaxis=dict(title='distritos'),
       yaxis=dict(title='euros'),
       showlegend=False
    )

In [36]:
fig = px.box(df, y="price_euro",x= 'neighbourhood', template="plotly_dark")
fig.show()

In [37]:
df['price'].mean()

2007.3427869207972

In [38]:
df['price_euro'].mean()

91.12146695260356

In [52]:
dfprice_meand = pd.DataFrame(price_mean)
dfneighbourhood2 = dfprice_meand.reset_index()
adam = gpd.read_file("data/neighbourhoods.geojson")
fig3 = px.choropleth_mapbox(dfneighbourhood2, geojson=adam, featureidkey='properties.neighbourhood',locations ="neighbourhood",color = 'price_euro', 
                            color_continuous_scale='magma', title="Precio Promedio por Distrito",zoom=10, hover_data = ['neighbourhood','price_euro'],
                            mapbox_style="carto-positron",width=1000, height=750,center = {"lat": 41.0037, "lon": 28.9737})
fig3.update(layout_coloraxis_showscale=True)
fig3.update_layout( paper_bgcolor="#fff",font_color="#AF1D56",title_font_size=40, title_x = 0.5)
fig3.show()

In [53]:
dfneighbourhood2

neighbourhood  price_euro
0         Esenler       23.55
1        Gungoren       39.27
2     Sultanbeyli       41.61
3         Avcilar       45.95
4       Kagithane       48.76
5      Sultangazi       52.25
6         Maltepe       57.61
7        Umraniye       58.84
8      Bayrampasa       59.97
9     Zeytinburnu       63.47
10         Kartal       64.25
11     Arnavutkoy       64.83
12       Atasehir       66.48
13       Bagcilar       68.85
14       Esenyurt       71.28
15       Bakirkoy       71.77
16         Pendik       76.64
17       Cekmekoy       77.39
18        Uskudar       79.08
19  Gaziosmanpasa       81.62
20          Sisli       82.55
21           Eyup       84.05
22     Basaksehir       84.19
23         Adalar       84.40
24   Kucukcekmece       85.37
25   Bahcelievler       87.26
26        Beyoglu       88.11
27          Fatih       91.03
28           Sile      106.65
29        Kadikoy      108.30
30        Catalca      110.84
31        Sariyer      124.35
32       Besiktas      125.33
33     Sancaktepe      130.38
34        Silivri      139.71
35   Buyukcekmece      158.00
36         Beykoz      165.08
37          Tuzla      320.59
38     Beylikduzu      344.29

### ¿Qué tipos de alojamientos se ofrecen?

En el análisis de los alojamientos ofrecidos en Estambul, podemos observar a través de este gráfico la diversidad de opciones disponibles. Se pueden identificar diferentes tipos de habitaciones, así como una amplia variedad de tipos de propiedades.

En cuanto a los **tipos de habitación**, encontramos las siguientes categorías.
Por un lado, están los tipos de habitación: 
* Entire home/apt - (**Casa/apartamento completo**)
* Private room - (**Habitación privada**)
* Hotel room - (**Habitación de hotel**)
* Shared room - (**Habitación compartida**)

Por otro lado, en cuanto a los **tipos de propiedad**, se identifican 109 categorías diferentes. Estas van desde "Entire serviced apartment" (apartamento completo con servicio) hasta "Private room in tent" (habitación privada en tienda de campaña), lo que demuestra la amplia gama de opciones disponibles para los visitantes.

Con el tercer gráfico podemos destacar que el tipo de propiedad que predomina en Estambul es "Casa/apartamento completo" y "Entire rental unit", que representa más de la mitad de los alojamientos registrados. Esto indica que la mayoría de los viajeros prefieren tener un espacio privado y completo durante su estancia en la ciudad.
 



In [40]:
rooms = df.groupby(['neighbourhood', 'room_type','property_type','accommodates']).size().reset_index(name='Count')

# Crear el gráfico de barras agrupadas
fig = px.treemap(rooms, path=['room_type','property_type'], values='Count', 
                 color_discrete_sequence=colors, template='plotly_dark')

fig.update_layout(
    title='Distribución por tipo de habitación y tipo de propiedad',
    xaxis=dict(title='Edad'),
    yaxis=dict(title='Cantidad'),
    bargap=0.1,
    showlegend=True
)
fig.show()


In [41]:
df['room_type'].unique()

array(['Entire home/apt', 'Private room', 'Hotel room', 'Shared room'],
      dtype=object)

In [42]:
# df['property_type'].unique()

In [43]:
fig5 = px.histogram(df,'room_type',
             nbins = 20,
             template= "plotly_dark",
             color_discrete_sequence = [colors[1]])

fig5.update_layout(
       title='Tipos de habitación',
    #    xaxis=dict(title='room_type'),
    #    yaxis=dict(title='Count'),
       showlegend=False
)
fig5.show()

In [44]:
# Cantidad de Barios

propertytype=df['property_type'].value_counts().sort_values(ascending=False).head(10)
fig1 = px.bar(propertytype, 
       template= "plotly_dark",
       color_discrete_sequence = [colors[3]],
    #    height=800    
       )
fig1.update_layout(
       title='Tipos de habitación (Top 10)',
       # xaxis=dict(title='Property_type'),
       # yaxis=dict(title='Count'),
       # showlegend=False
)

### ¿Cómo son los propietarios?

Se llevó el análisis en función de las calificaciones y reseñas que presentan los propietarios.

* En primer lugar, se examinó si los huéspedes mostraban preferencia por los anfitriones con la calificación de "Superhost". Sin embargo, se observó que los usuarios no presentaban preferencia por los Superhosts, ya que la mayoría de las reseñas dadas corresponde a los que no tienen calificación Superhost. Dentro de este análisis podemos ver que predominan las calificaciones en el rango de 4 a 5 en ambas categorías.

* Posteriormente, se analizó la distribución de las respuestas de los anfitriones en función de la cantidad de reseñas recibidas. Específicamente, se examinaron los diferentes tipos de respuestas que ofrecen los anfitriones en relación con su tiempo de respuesta. Se observó que aquellos anfitriones que brindaban respuestas dentro de una hora tenían una mayor cantidad de reseñas en comparación con aquellos que tenían tiempos de respuesta más prolongados.
Este hallazgo sugiere que la rapidez en la respuesta por parte de los anfitriones puede ser un indicador relevante al seleccionar alojamientos. Los huéspedes parecen valorar y apreciar una respuesta rápida, lo que puede influir en la decisión de reservar con un determinado anfitrión.


In [45]:
df['host_is_superhost'] = df['host_is_superhost'].replace({"t": "Superhost", "f": "No_superhost"})
feq=df['host_is_superhost'].value_counts()

px.pie(feq ,names = feq.index, values=feq.values,width = 1000, 
       template= "plotly_dark",
       color_discrete_sequence = colors,
       title="Number of listings with Superhost")

In [46]:
sh_reviews1 = df[['host_is_superhost','review_scores_value']].value_counts().reset_index().head(15)

In [47]:
fig7 = px.box(df, x="review_scores_value",y= 'host_is_superhost',
              template="plotly_dark",
              color_discrete_sequence = colors
              )

fig7.update_layout(
    title='Numero de Reseñas',
    xaxis=dict(title='Calificaciones'),
    yaxis=dict(title=''),
    bargap=0.1,
    showlegend=True 
    )
fig7.show()

In [48]:
response_time_rates = df.groupby(["host_response_time", 'review_scores_value'])["host_response_rate"].mean().reset_index()
response_time_rates.head()

host_response_time  review_scores_value  host_response_rate
0  a few days or more                 1.00           10.577778
1  a few days or more                 1.33            0.000000
2  a few days or more                 1.50           11.000000
3  a few days or more                 2.00            0.000000
4  a few days or more                 2.25            0.000000

In [49]:

fig8 = px.histogram(response_time_rates,x='host_response_time' ,y="review_scores_value", 
                   template="plotly_dark", 
                   marginal="box", 
                   hover_data=response_time_rates.columns,
                    color_discrete_sequence = [colors[3]]
                    )
                   
fig8.update_layout(
                    title='Distribución de puntuaciones de huéspedes por tiempo de respuesta del anfitrión',
                    xaxis=dict(title='Tiempo de respuesta'),
                    yaxis=dict(title='Puntuaciones de huéspedes'),
                    bargap=0.1,
                    showlegend=True 
                    )
fig8.show()
                   

# 7. conclusiones

Después analizar nuestras variables relacionada con la oferta de alojamientos en la ciudad de Estambul, podemos llegar a las siguientes conclusiones:

* Oferta de Alojamientos: En Estambul, se encuentran disponibles un total de 41,500 alojamientos en la plataforma Airbnb. Esta cifra refleja una amplia variedad de opciones para los viajeros que visitan la ciudad.

* Distritos Populares: Los distritos más destacados en términos de oferta de alojamientos son Beyoglu, Sisli, Kadikoy y Fatih. Estos distritos destacan por tener una amplia variedad de opciones para los viajeros.

* Precio Medio: El precio medio por noche de alojamiento en Estambul es de €91.12. Esta cifra proporciona una referencia útil para los viajeros que deseen planificar su presupuesto de alojamiento en la ciudad.

* Tipo de Alojamiento: El tipo de alojamiento más comúnmente ofrecido en Estambul es el "Casa/apartamento completo". Esto implica que la mayoría de los alojamientos disponibles son unidades residenciales completas que brindan privacidad y comodidad a los huéspedes.

* Calificación y Respuestas de los Anfitriones: Aunque los Superhosts reciben reconocimiento por su excelencia en el servicio, no se observa una preferencia marcada por parte de los huéspedes hacia ellos. Sin embargo, se destaca la importancia de una pronta respuesta por parte de los anfitriones, ya que aquellos que responden rápidamente suelen recibir más reseñas de los huéspedes.

* Estas conclusiones nos brindan una idea general sobre la oferta de alojamientos en Estambul a través de Airbnb y nos ayudan a comprender mejor el mercado de alojamiento en la ciudad.

En cuanto a futuros análisis, se puede profundizar en el análisis de variables relacionadas con las reseñas:

* Como el sentimiento de los comentarios y su relación con la calificación de los anfitriones.
* También es posible examinar las regulaciones y restricciones aplicables a los anfitriones en la ciudad, lo cual podría proporcionar una perspectiva adicional sobre el mercado de alojamiento en Estambul.


Guardado de DT final

In [50]:
# Dataset para app
#guardamos nuestro df 
# df.to_csv('df_limpio.csv', header=True, index=False) 

In [51]:
# Dataset para powerBi
# #guardamos nuestro df 
# df.to_csv('df_powerbi.csv', header=True, index=False) 